In [1]:
import numpy as np
import pandas as pd
import xgboost as xgb
from helpers.rmse import rmse
from sklearn.model_selection import train_test_split
from bayes_opt import BayesianOptimization
import gc

In [2]:
# fix seed
SEED = 123
np.random.seed(SEED)

In [3]:
train = pd.read_csv('data/train_abt.csv')

X = train.drop('log_trip_duration', axis=1).values
y = train.log_trip_duration.values

# Train test split
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2, random_state=SEED)

# Convert data to XGBoost data format 
d_train = xgb.DMatrix(X_train, label=y_train)
d_valid = xgb.DMatrix(X_valid, label=y_valid)

In [4]:
def xgb_evaluate(min_child_weight,
                 colsample_bytree,
                 max_depth,
                 subsample,
                 gamma,
                 alpha):
    
    
    params = {}
    params['min_child_weight'] = int(min_child_weight)
    params['colsample_bytree'] = max(min(colsample_bytree, 1), 0)
    params['max_depth'] = int(max_depth)
    params['subsample'] = max(min(subsample, 1), 0)
    params['gamma'] = max(gamma, 0)
    params['alpha'] = max(alpha, 0)
    params['objective'] = 'reg:linear' 
    params['eval_metric'] = 'rmse'      
    params['silent'] = 1                
    params['tree_method'] = 'hist'
    params['eta'] = 0.1            
    params['seed'] = SEED

    watchlist = [(d_train, 'train'), (d_valid, 'valid')]
    reg = xgb.train(params, d_train, 10000, watchlist, early_stopping_rounds=50)  
    
    pred = reg.predict(d_valid, ntree_limit=reg.best_ntree_limit)
    gc.collect()
    
    # Bayesian optimization can only maximize the score, Thus, we need the negative error
    return -1 * rmse(y_valid, pred)

In [5]:
# Numbers of exploration times before optimization
init_points = 15
# Numbers of optimization times 
num_iter = 25

xgbBO = BayesianOptimization(xgb_evaluate, {'min_child_weight': (1, 20),
                                                'colsample_bytree': (0.1, 1),
                                                'max_depth': (5, 15),
                                                'subsample': (0.5, 1),
                                                'gamma': (0, 10),
                                                'alpha': (0, 10),
                                                })

xgbBO.maximize(init_points=init_points, n_iter=num_iter)

Initialization
---------------------------------------------------------------------------------------------------------------------------
 Step |   Time |      Value |     alpha |   colsample_bytree |     gamma |   max_depth |   min_child_weight |   subsample | 
[01:37:24] Tree method is selected to be 'hist', which uses a single updater grow_fast_histmaker.
[0]	train-rmse:5.42223	valid-rmse:5.42203
Multiple eval metrics have been passed: 'valid-rmse' will be used for early stopping.

Will train until valid-rmse hasn't improved in 50 rounds.
[1]	train-rmse:4.88872	valid-rmse:4.88852
[2]	train-rmse:4.40534	valid-rmse:4.4052
[3]	train-rmse:3.97052	valid-rmse:3.97043
[4]	train-rmse:3.58438	valid-rmse:3.58433
[5]	train-rmse:3.23269	valid-rmse:3.23274
[6]	train-rmse:2.92161	valid-rmse:2.9217
[7]	train-rmse:2.63774	valid-rmse:2.63791
[8]	train-rmse:2.38766	valid-rmse:2.38783
[9]	train-rmse:2.15932	valid-rmse:2.15957
[10]	train-rmse:1.95448	valid-rmse:1.95479
[11]	train-rmse:1.77115	valid-rm

[171]	train-rmse:0.41593	valid-rmse:0.422586
[172]	train-rmse:0.415898	valid-rmse:0.422556
[173]	train-rmse:0.415882	valid-rmse:0.422539
[174]	train-rmse:0.415773	valid-rmse:0.422441
[175]	train-rmse:0.415707	valid-rmse:0.422374
[176]	train-rmse:0.415647	valid-rmse:0.422315
[177]	train-rmse:0.415578	valid-rmse:0.422276
[178]	train-rmse:0.415437	valid-rmse:0.422161
[179]	train-rmse:0.415332	valid-rmse:0.422061
[180]	train-rmse:0.415286	valid-rmse:0.422038
[181]	train-rmse:0.415266	valid-rmse:0.422019
[182]	train-rmse:0.415232	valid-rmse:0.421996
[183]	train-rmse:0.415109	valid-rmse:0.421896
[184]	train-rmse:0.415061	valid-rmse:0.421856
[185]	train-rmse:0.414894	valid-rmse:0.421716
[186]	train-rmse:0.414784	valid-rmse:0.421613
[187]	train-rmse:0.414663	valid-rmse:0.42151
[188]	train-rmse:0.414623	valid-rmse:0.421469
[189]	train-rmse:0.414573	valid-rmse:0.421447
[190]	train-rmse:0.414531	valid-rmse:0.421412
[191]	train-rmse:0.414394	valid-rmse:0.421311
[192]	train-rmse:0.414381	valid-rmse

[350]	train-rmse:0.407989	valid-rmse:0.41621
[351]	train-rmse:0.40795	valid-rmse:0.416187
[352]	train-rmse:0.40795	valid-rmse:0.416187
[353]	train-rmse:0.407896	valid-rmse:0.416207
[354]	train-rmse:0.407887	valid-rmse:0.416194
[355]	train-rmse:0.407852	valid-rmse:0.416164
[356]	train-rmse:0.407805	valid-rmse:0.41613
[357]	train-rmse:0.407769	valid-rmse:0.416124
[358]	train-rmse:0.407746	valid-rmse:0.416111
[359]	train-rmse:0.407566	valid-rmse:0.415936
[360]	train-rmse:0.407515	valid-rmse:0.41591
[361]	train-rmse:0.407501	valid-rmse:0.415898
[362]	train-rmse:0.407493	valid-rmse:0.41589
[363]	train-rmse:0.407415	valid-rmse:0.41587
[364]	train-rmse:0.407363	valid-rmse:0.415818
[365]	train-rmse:0.407305	valid-rmse:0.415773
[366]	train-rmse:0.407278	valid-rmse:0.415748
[367]	train-rmse:0.407257	valid-rmse:0.415729
[368]	train-rmse:0.407247	valid-rmse:0.415721
[369]	train-rmse:0.407241	valid-rmse:0.415717
[370]	train-rmse:0.407183	valid-rmse:0.415661
[371]	train-rmse:0.407169	valid-rmse:0.41

[529]	train-rmse:0.403828	valid-rmse:0.413581
[530]	train-rmse:0.403828	valid-rmse:0.413581
[531]	train-rmse:0.403781	valid-rmse:0.41354
[532]	train-rmse:0.403764	valid-rmse:0.413522
[533]	train-rmse:0.403632	valid-rmse:0.413392
[534]	train-rmse:0.403626	valid-rmse:0.413398
[535]	train-rmse:0.403571	valid-rmse:0.413347
[536]	train-rmse:0.403571	valid-rmse:0.413347
[537]	train-rmse:0.403536	valid-rmse:0.413328
[538]	train-rmse:0.403536	valid-rmse:0.413329
[539]	train-rmse:0.403536	valid-rmse:0.413328
[540]	train-rmse:0.403536	valid-rmse:0.413328
[541]	train-rmse:0.403528	valid-rmse:0.41332
[542]	train-rmse:0.403528	valid-rmse:0.41332
[543]	train-rmse:0.403522	valid-rmse:0.413315
[544]	train-rmse:0.403491	valid-rmse:0.413287
[545]	train-rmse:0.403491	valid-rmse:0.413287
[546]	train-rmse:0.403478	valid-rmse:0.413274
[547]	train-rmse:0.40347	valid-rmse:0.413273
[548]	train-rmse:0.40347	valid-rmse:0.413273
[549]	train-rmse:0.403377	valid-rmse:0.41323
[550]	train-rmse:0.403369	valid-rmse:0.4

[708]	train-rmse:0.400885	valid-rmse:0.411981
[709]	train-rmse:0.400885	valid-rmse:0.411981
[710]	train-rmse:0.400872	valid-rmse:0.411988
[711]	train-rmse:0.400847	valid-rmse:0.41198
[712]	train-rmse:0.400847	valid-rmse:0.41198
[713]	train-rmse:0.400847	valid-rmse:0.41198
[714]	train-rmse:0.400847	valid-rmse:0.41198
[715]	train-rmse:0.400802	valid-rmse:0.41195
[716]	train-rmse:0.400795	valid-rmse:0.411946
[717]	train-rmse:0.400789	valid-rmse:0.411943
[718]	train-rmse:0.400771	valid-rmse:0.411946
[719]	train-rmse:0.400771	valid-rmse:0.411946
[720]	train-rmse:0.400739	valid-rmse:0.411928
[721]	train-rmse:0.400715	valid-rmse:0.411916
[722]	train-rmse:0.400715	valid-rmse:0.411916
[723]	train-rmse:0.400705	valid-rmse:0.411909
[724]	train-rmse:0.400662	valid-rmse:0.411874
[725]	train-rmse:0.400662	valid-rmse:0.411874
[726]	train-rmse:0.400662	valid-rmse:0.411874
[727]	train-rmse:0.400656	valid-rmse:0.41187
[728]	train-rmse:0.400633	valid-rmse:0.411847
[729]	train-rmse:0.400633	valid-rmse:0.4

...

[177]	train-rmse:0.374654	valid-rmse:0.399606
[178]	train-rmse:0.374495	valid-rmse:0.399518
[179]	train-rmse:0.374275	valid-rmse:0.39948
[180]	train-rmse:0.374073	valid-rmse:0.399388
[181]	train-rmse:0.373852	valid-rmse:0.399361
[182]	train-rmse:0.373702	valid-rmse:0.39932
[183]	train-rmse:0.373539	valid-rmse:0.399263
[184]	train-rmse:0.373295	valid-rmse:0.39924
[185]	train-rmse:0.373094	valid-rmse:0.399129
[186]	train-rmse:0.372914	valid-rmse:0.399066
[187]	train-rmse:0.372806	valid-rmse:0.399038
[188]	train-rmse:0.372733	valid-rmse:0.398994
[189]	train-rmse:0.372541	valid-rmse:0.39892
[190]	train-rmse:0.372423	valid-rmse:0.398876
[191]	train-rmse:0.372265	valid-rmse:0.398849
[192]	train-rmse:0.372089	valid-rmse:0.398807
[193]	train-rmse:0.371974	valid-rmse:0.398752
[194]	train-rmse:0.371934	valid-rmse:0.398735
[195]	train-rmse:0.37188	valid-rmse:0.39872
[196]	train-rmse:0.371701	valid-rmse:0.398602
[197]	train-rmse:0.371514	valid-rmse:0.39858
[198]	train-rmse:0.371355	valid-rmse:0.39

[357]	train-rmse:0.350481	valid-rmse:0.392702
[358]	train-rmse:0.350332	valid-rmse:0.392699
[359]	train-rmse:0.35024	valid-rmse:0.392692
[360]	train-rmse:0.350131	valid-rmse:0.392678
[361]	train-rmse:0.350048	valid-rmse:0.392672
[362]	train-rmse:0.349958	valid-rmse:0.39265
[363]	train-rmse:0.349816	valid-rmse:0.392636
[364]	train-rmse:0.349749	valid-rmse:0.392612
[365]	train-rmse:0.349612	valid-rmse:0.392604
[366]	train-rmse:0.349446	valid-rmse:0.392587
[367]	train-rmse:0.34929	valid-rmse:0.392511
[368]	train-rmse:0.349241	valid-rmse:0.392502
[369]	train-rmse:0.349102	valid-rmse:0.392494
[370]	train-rmse:0.348962	valid-rmse:0.392471
[371]	train-rmse:0.348835	valid-rmse:0.392469
[372]	train-rmse:0.348693	valid-rmse:0.392412
[373]	train-rmse:0.34856	valid-rmse:0.392399
[374]	train-rmse:0.348487	valid-rmse:0.392374
[375]	train-rmse:0.348377	valid-rmse:0.392361
[376]	train-rmse:0.348275	valid-rmse:0.392346
[377]	train-rmse:0.348211	valid-rmse:0.392318
[378]	train-rmse:0.348098	valid-rmse:0

[536]	train-rmse:0.334365	valid-rmse:0.390918
[537]	train-rmse:0.334268	valid-rmse:0.390896
[538]	train-rmse:0.334142	valid-rmse:0.390869
[539]	train-rmse:0.334041	valid-rmse:0.390869
[540]	train-rmse:0.333977	valid-rmse:0.390858
[541]	train-rmse:0.333926	valid-rmse:0.390866
[542]	train-rmse:0.333839	valid-rmse:0.390845
[543]	train-rmse:0.333716	valid-rmse:0.390833
[544]	train-rmse:0.333654	valid-rmse:0.390824
[545]	train-rmse:0.333585	valid-rmse:0.390803
[546]	train-rmse:0.333524	valid-rmse:0.390811
[547]	train-rmse:0.333464	valid-rmse:0.390822
[548]	train-rmse:0.333374	valid-rmse:0.390809
[549]	train-rmse:0.333293	valid-rmse:0.390827
[550]	train-rmse:0.333209	valid-rmse:0.390849
[551]	train-rmse:0.333132	valid-rmse:0.390859
[552]	train-rmse:0.333063	valid-rmse:0.390844
[553]	train-rmse:0.332981	valid-rmse:0.390846
[554]	train-rmse:0.332915	valid-rmse:0.390842
[555]	train-rmse:0.332811	valid-rmse:0.390814
[556]	train-rmse:0.332728	valid-rmse:0.390805
[557]	train-rmse:0.332641	valid-rm

[716]	train-rmse:0.321869	valid-rmse:0.390572
[717]	train-rmse:0.321809	valid-rmse:0.390572
[718]	train-rmse:0.321735	valid-rmse:0.390578
[719]	train-rmse:0.321692	valid-rmse:0.39057
[720]	train-rmse:0.321609	valid-rmse:0.390575
[721]	train-rmse:0.321542	valid-rmse:0.390584
[722]	train-rmse:0.321495	valid-rmse:0.390586
[723]	train-rmse:0.321437	valid-rmse:0.390589
[724]	train-rmse:0.321382	valid-rmse:0.390583
[725]	train-rmse:0.321299	valid-rmse:0.390562
[726]	train-rmse:0.321227	valid-rmse:0.390558
[727]	train-rmse:0.321202	valid-rmse:0.390559
[728]	train-rmse:0.321126	valid-rmse:0.39058
[729]	train-rmse:0.321051	valid-rmse:0.390574
[730]	train-rmse:0.320972	valid-rmse:0.390559
[731]	train-rmse:0.320886	valid-rmse:0.390569
[732]	train-rmse:0.320795	valid-rmse:0.390566
[733]	train-rmse:0.320745	valid-rmse:0.390567
[734]	train-rmse:0.320689	valid-rmse:0.390577
[735]	train-rmse:0.320634	valid-rmse:0.390586
[736]	train-rmse:0.320591	valid-rmse:0.390584
[737]	train-rmse:0.320524	valid-rmse

C:\Users\John\Anaconda3\lib\site-packages\sklearn\gaussian_process\gpr.py:457: UserWarning: fmin_l_bfgs_b terminated abnormally with the  state: {'grad': array([0.00117037]), 'task': b'ABNORMAL_TERMINATION_IN_LNSRCH', 'funcalls': 61, 'nit': 5, 'warnflag': 2}
  " state: %s" % convergence_dict)


In [15]:
# Display the best parameters
xgbBO.res['max']

{'max_val': -0.3892582586569608,
 'max_params': {'min_child_weight': 18.430128633166355,
  'colsample_bytree': 0.9342301218049115,
  'max_depth': 12.934454306902602,
  'subsample': 0.9985240961242587,
  'gamma': 0.06841258698166541,
  'alpha': 8.64181220876009}}

In [23]:
# Display all iterations in dataframe
history_df = pd.DataFrame(xgbBO.res['all']['params'])
history_df2 = pd.DataFrame(xgbBO.res['all']['values'])
history_df = pd.concat((history_df, history_df2), axis=1)
history_df.rename(columns = { 0 : 'rmse'}, inplace=True)
history_df.sort_values('rmse',ascending=False)

alpha  colsample_bytree     gamma  max_depth  min_child_weight  \
22  8.641812          0.934230  0.068413  12.934454         18.430129   
20  9.906744          0.995120  0.072458  11.783581          7.468133   
15  8.079491          0.871953  0.098828  14.036554         17.958747   
8   7.653326          0.952183  0.002713  10.905306         19.345309   
13  6.207357          0.988696  0.064897  13.390670          3.250097   
16  8.086154          0.911794  0.002871  14.859271          2.757554   
18  9.110834          0.990859  0.244110  14.715631          1.476080   
4   9.988177          0.933152  0.205162  13.711243         17.817263   
14  4.322140          0.940288  0.023073  14.207139         18.806763   
17  5.344455          0.985597  0.020928  14.998658          1.554996   
23  8.750476          0.998666  0.023839  14.750356         11.978598   
6   8.394268          0.977915  0.093132  13.793235          8.317338   
24  8.609891          0.974168  0.020619  14.045442         16.982483   
5   6.279253          0.975782  0.145940  14.953877         15.554147   
21  7.722471          0.626220  0.043239  13.661645         18.705226   
10  8.766975          0.912700  0.481470  13.267048         19.459651   
19  9.657273          0.908822  0.663340  14.840946         15.455393   
1   9.299851          0.963183  0.064338  14.953648          1.331496   
9   9.632643          0.959602  0.076832  11.019649         16.280430   
7   9.823408          0.852464  0.179888  10.903051          1.094921   
3   4.304086          0.856752  0.078099  14.563622         19.770144   
12  0.960623          0.944337  0.109110  12.111550          1.492935   
0   9.870698          0.697730  0.572376   6.521506         19.925521   
2   0.204330          0.980248  4.559234  14.338235          1.662230   
11  0.705438          0.917630  0.565604   6.035619         19.702276   

    subsample      rmse  
22   0.998524 -0.389258  
20   0.993383 -0.389546  
15   0.997215 -0.389623  
8    0.994560 -0.389800  
13   0.987117 -0.389802  
16   0.984083 -0.389814  
18   0.994307 -0.389968  
4    0.983366 -0.390015  
14   0.999136 -0.390040  
17   0.980029 -0.390111  
23   0.973009 -0.390376  
6    0.981304 -0.390457  
24   0.935181 -0.390520  
5    0.962678 -0.390564  
21   0.994291 -0.390651  
10   0.981397 -0.391072  
19   0.991691 -0.391267  
1    0.871850 -0.391468  
9    0.934732 -0.391665  
7    0.969170 -0.391900  
3    0.892308 -0.391956  
12   0.998931 -0.392612  
0    0.992585 -0.394816  
2    0.984907 -0.396641  
11   0.944017 -0.398683